# This is week-3 capstone project - Segmenting and clustering neighborhoods in Toronto
### Svavar Berg Jóhannsson

In [1]:
!conda install -c conda-forge beautifulsoup4 --yes

!conda install -c conda-forge geopy --yes

!conda install -c conda-forge folium=0.5.0 --yes

print('Libraries installed!')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - beautifulsoup4


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    beautifulsoup4-4.9.1       |   py36h9f0ad1d_0         163 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.6 MB

The following NEW packages will be INSTALLED:

    python_abi:      3.6-1_cp36m       conda-forge

The following packages will be UPDATED:

    beautifulsoup4:  4.7.1-py36_1                

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import requests # library to handle requests

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib as mp

# import k-means from clustering stage
from sklearn.cluster import KMeans

#CSV
import csv

#BeautifulSoup for webscraping
from bs4 import BeautifulSoup

from geopy.geocoders import Nominatim
import folium
import json


print('Libraries imported.')

Libraries imported.


## Scrape the HTML 
Here we want neighborhoods in Toronto area and they start with M so we use the link: https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M
We both use requests and BS4 to get the data. 
Then we go through it to append it into three tables: postalCode, borough and neighborhood.
    

In [3]:
#URL to webscrape
url = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text
soup = BeautifulSoup(url, 'html.parser')

postalCode = []
borough = []
neighborhood = []

for row in soup.find('table').find_all('tr'):
    cells = row.find_all('td')
    if(len(cells) > 0):
        postalCode.append(cells[0].text.rstrip('\n'))
        borough.append(cells[1].text.rstrip('\n'))
        neighborhood.append(cells[2].text.rstrip('\n'))



## Get data into DataFrame
Then we need to get those three lists into a dataframe 

In [4]:
torontoNeighborhoods = [('PostalCode', postalCode),
                       ('Borough', borough),
                       ('Neighborhood', neighborhood)]
df_toronto = pd.DataFrame.from_dict(dict(torontoNeighborhoods))
df_toronto.head(25)

PostalCode           Borough  \
0         M1A      Not assigned   
1         M2A      Not assigned   
2         M3A        North York   
3         M4A        North York   
4         M5A  Downtown Toronto   
5         M6A        North York   
6         M7A  Downtown Toronto   
7         M8A      Not assigned   
8         M9A         Etobicoke   
9         M1B       Scarborough   
10        M2B      Not assigned   
11        M3B        North York   
12        M4B         East York   
13        M5B  Downtown Toronto   
14        M6B        North York   
15        M7B      Not assigned   
16        M8B      Not assigned   
17        M9B         Etobicoke   
18        M1C       Scarborough   
19        M2C      Not assigned   
20        M3C        North York   
21        M4C         East York   
22        M5C  Downtown Toronto   
23        M6C              York   
24        M7C      Not assigned   

                                         Neighborhood  
0                                        Not assigned  
1                                        Not assigned  
2                                           Parkwoods  
3                                    Victoria Village  
4                           Regent Park, Harbourfront  
5                    Lawrence Manor, Lawrence Heights  
6         Queen's Park, Ontario Provincial Government  
7                                        Not assigned  
8             Islington Avenue, Humber Valley Village  
9                                      Malvern, Rouge  
10                                       Not assigned  
11                                          Don Mills  
12                    Parkview Hill, Woodbine Gardens  
13                           Garden District, Ryerson  
14                                          Glencairn  
15                                       Not assigned  
16                                       Not assigned  
17  West Deane Park, Princess Gardens, Martin Grov...  
18             Rouge Hill, Port Union, Highland Creek  
19                                       Not assigned  
20                                          Don Mills  
21                                   Woodbine Heights  
22                                     St. James Town  
23                                 Humewood-Cedarvale  
24                                       Not assigned

Cleaning the dataset 
Remvoing all the cells that have "Not Assigned" in Neighborhoods

In [5]:
df_toronto['Borough'].replace('Not assigned', np.nan, inplace=True)
df_toronto.dropna(subset=['Borough'], axis=0, inplace=True)
df_toronto.head(25)

PostalCode           Borough  \
2         M3A        North York   
3         M4A        North York   
4         M5A  Downtown Toronto   
5         M6A        North York   
6         M7A  Downtown Toronto   
8         M9A         Etobicoke   
9         M1B       Scarborough   
11        M3B        North York   
12        M4B         East York   
13        M5B  Downtown Toronto   
14        M6B        North York   
17        M9B         Etobicoke   
18        M1C       Scarborough   
20        M3C        North York   
21        M4C         East York   
22        M5C  Downtown Toronto   
23        M6C              York   
26        M9C         Etobicoke   
27        M1E       Scarborough   
30        M4E      East Toronto   
31        M5E  Downtown Toronto   
32        M6E              York   
36        M1G       Scarborough   
39        M4G         East York   
40        M5G  Downtown Toronto   

                                         Neighborhood  
2                                           Parkwoods  
3                                    Victoria Village  
4                           Regent Park, Harbourfront  
5                    Lawrence Manor, Lawrence Heights  
6         Queen's Park, Ontario Provincial Government  
8             Islington Avenue, Humber Valley Village  
9                                      Malvern, Rouge  
11                                          Don Mills  
12                    Parkview Hill, Woodbine Gardens  
13                           Garden District, Ryerson  
14                                          Glencairn  
17  West Deane Park, Princess Gardens, Martin Grov...  
18             Rouge Hill, Port Union, Highland Creek  
20                                          Don Mills  
21                                   Woodbine Heights  
22                                     St. James Town  
23                                 Humewood-Cedarvale  
26  Eringate, Bloordale Gardens, Old Burnhamthorpe...  
27                  Guildwood, Morningside, West Hill  
30                                        The Beaches  
31                                        Berczy Park  
32                                Caledonia-Fairbanks  
36                                             Woburn  
39                                            Leaside  
40                                 Central Bay Street

Grouping neighborhoods together
More than one neighborhood can be within postal code area so we need to group them together.

In [6]:
df_TN = df_toronto.groupby(['PostalCode', 'Borough'])['Neighborhood'].apply(','.join).reset_index()

Further cleaning the data
Dealing with not assigned neighborhoods can be problematic so I've decided to replace "not assigned" with corresponding Borough.

In [7]:
df_TN['Neighborhood'].replace('Not assigned', 'Borough', inplace=True)
df_TN.head(20)

PostalCode      Borough                                       Neighborhood
0         M1B  Scarborough                                     Malvern, Rouge
1         M1C  Scarborough             Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough                  Guildwood, Morningside, West Hill
3         M1G  Scarborough                                             Woburn
4         M1H  Scarborough                                          Cedarbrae
5         M1J  Scarborough                                Scarborough Village
6         M1K  Scarborough        Kennedy Park, Ionview, East Birchmount Park
7         M1L  Scarborough                    Golden Mile, Clairlea, Oakridge
8         M1M  Scarborough    Cliffside, Cliffcrest, Scarborough Village West
9         M1N  Scarborough                        Birch Cliff, Cliffside West
10        M1P  Scarborough  Dorset Park, Wexford Heights, Scarborough Town...
11        M1R  Scarborough                                  Wexford, Maryvale
12        M1S  Scarborough                                          Agincourt
13        M1T  Scarborough            Clarks Corners, Tam O'Shanter, Sullivan
14        M1V  Scarborough  Milliken, Agincourt North, Steeles East, L'Amo...
15        M1W  Scarborough                      Steeles West, L'Amoreaux West
16        M1X  Scarborough                                        Upper Rouge
17        M2H   North York                                  Hillcrest Village
18        M2J   North York                       Fairview, Henry Farm, Oriole
19        M2K   North York                                    Bayview Village

## Cleaning the DataFrame
We create new dataframe with cleaned data and use shape to print the numbers of rows within our dataframe.

In [8]:
df_clean = df_TN
df_clean.shape

(103, 3)

## Second part:
We need to get coordinates and add them to existing DataFrame

In [9]:
geo_data = ('http://cocl.us/Geospatial_data')
df_geoData = pd.read_csv(geo_data)
df_geoData.columns = ['PostalCode','Latitude','Longitude']
df_geoData.head()



PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

## Merging together
Merge the two tables together on PostalCode

In [10]:
df_geoData = pd.merge(df_clean, df_geoData, on='PostalCode')
df_geoData

PostalCode           Borough  \
0          M1B       Scarborough   
1          M1C       Scarborough   
2          M1E       Scarborough   
3          M1G       Scarborough   
4          M1H       Scarborough   
5          M1J       Scarborough   
6          M1K       Scarborough   
7          M1L       Scarborough   
8          M1M       Scarborough   
9          M1N       Scarborough   
10         M1P       Scarborough   
11         M1R       Scarborough   
12         M1S       Scarborough   
13         M1T       Scarborough   
14         M1V       Scarborough   
15         M1W       Scarborough   
16         M1X       Scarborough   
17         M2H        North York   
18         M2J        North York   
19         M2K        North York   
20         M2L        North York   
21         M2M        North York   
22         M2N        North York   
23         M2P        North York   
24         M2R        North York   
25         M3A        North York   
26         M3B        North York   
27         M3C        North York   
28         M3H        North York   
29         M3J        North York   
30         M3K        North York   
31         M3L        North York   
32         M3M        North York   
33         M3N        North York   
34         M4A        North York   
35         M4B         East York   
36         M4C         East York   
37         M4E      East Toronto   
38         M4G         East York   
39         M4H         East York   
40         M4J         East York   
41         M4K      East Toronto   
42         M4L      East Toronto   
43         M4M      East Toronto   
44         M4N   Central Toronto   
45         M4P   Central Toronto   
46         M4R   Central Toronto   
47         M4S   Central Toronto   
48         M4T   Central Toronto   
49         M4V   Central Toronto   
50         M4W  Downtown Toronto   
51         M4X  Downtown Toronto   
52         M4Y  Downtown Toronto   
53         M5A  Downtown Toronto   
54         M5B  Downtown Toronto   
55         M5C  Downtown Toronto   
56         M5E  Downtown Toronto   
57         M5G  Downtown Toronto   
58         M5H  Downtown Toronto   
59         M5J  Downtown Toronto   
60         M5K  Downtown Toronto   
61         M5L  Downtown Toronto   
62         M5M        North York   
63         M5N   Central Toronto   
64         M5P   Central Toronto   
65         M5R   Central Toronto   
66         M5S  Downtown Toronto   
67         M5T  Downtown Toronto   
68         M5V  Downtown Toronto   
69         M5W  Downtown Toronto   
70         M5X  Downtown Toronto   
71         M6A        North York   
72         M6B        North York   
73         M6C              York   
74         M6E              York   
75         M6G  Downtown Toronto   
76         M6H      West Toronto   
77         M6J      West Toronto   
78         M6K      West Toronto   
79         M6L        North York   
80         M6M              York   
81         M6N              York   
82         M6P      West Toronto   
83         M6R      West Toronto   
84         M6S      West Toronto   
85         M7A  Downtown Toronto   
86         M7R       Mississauga   
87         M7Y      East Toronto   
88         M8V         Etobicoke   
89         M8W         Etobicoke   
90         M8X         Etobicoke   
91         M8Y         Etobicoke   
92         M8Z         Etobicoke   
93         M9A         Etobicoke   
94         M9B         Etobicoke   
95         M9C         Etobicoke   
96         M9L        North York   
97         M9M        North York   
98         M9N              York   
99         M9P         Etobicoke   
100        M9R         Etobicoke   
101        M9V         Etobicoke   
102        M9W         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                       Malvern, Rouge  43.806686 -79.194353  
1               Rouge Hill, Port Union, Highland Creek  43.784535 -79.160497  
2                    G

### Next: 
Let's explore and cluster the neighborhoods together. 

In [11]:
addr = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="tl-toronto-neigh")
location = geolocator.geocode(addr)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Toronto are 43.6534817, -79.3839347.


## Creating map with folium
Let's create a map with Folium with borough markers.

In [12]:
toronto_map = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, long, post, borough, neigh in zip(df_geoData['Latitude'], df_geoData['Longitude'], df_geoData['PostalCode'], df_geoData['Borough'], df_geoData['Neighborhood']):
    label = "{} ({}): {}".format(borough, post, neigh)
    popup = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius=5,
        popup=popup,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(toronto_map)
    
toronto_map

## Accessing FourSquare API:
    Now we access the FourSquare API to explore the Boroughs.

In [27]:
CLIENT_ID = 'JINXJXDKGLLTTSUIQM10IP4VPJIW52MKS0KSSD1MWP5QVEBY' # your Foursquare ID
CLIENT_SECRET = 'IFRXJIQXI3A51RHS2ZDWB1DMUWBXHUOEBNGNXVT3OX2JG5FE' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JINXJXDKGLLTTSUIQM10IP4VPJIW52MKS0KSSD1MWP5QVEBY
CLIENT_SECRET:IFRXJIQXI3A51RHS2ZDWB1DMUWBXHUOEBNGNXVT3OX2JG5FE


### Create the API request

In [28]:
LIMIT = 100
radius = 500

venues= []
for lat, long, post, borough, neighborhood in zip(df_geoData['Latitude'], df_geoData['Longitude'], df_geoData['PostalCode'], df_geoData['Borough'], df_geoData['Neighborhood']):
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat, 
        long, 
        radius, 
        LIMIT)
    
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    for venue in results:
        venues.append((
            post, 
            borough,
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [29]:
results

[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '5273f6f311d2137549494e29',
   'name': 'Economy Rent A Car',
   'location': {'lat': 43.708471,
    'lng': -79.589943,
    'labeledLatLngs': [{'label': 'display',
      'lat': 43.708471,
      'lng': -79.589943}],
    'distance': 382,
    'cc': 'CA',
    'country': 'Canada',
    'formattedAddress': ['Canada']},
   'categories': [{'id': '4bf58dd8d48988d1ef941735',
     'name': 'Rental Car Location',
     'pluralName': 'Rental Car Locations',
     'shortName': 'Rental Car',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/airport_rentalcar_',
      'suffix': '.png'},
     'primary': True}],
   'photos': {'count': 0, 'groups': []}},
  'referralId': 'e-0-5273f6f311d2137549494e29-0'},
 {'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'global

In [30]:
df_venues = pd.DataFrame(venues)
df_venues.head(10)

0            1                                       2          3  \
0  M1B  Scarborough                          Malvern, Rouge  43.806686   
1  M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2  M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
3  M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
4  M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
5  M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
6  M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
7  M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
8  M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
9  M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   

           4                             5          6          7  \
0 -79.194353                       Wendy’s  43.807448 -79.199056   
1 -79.160497   Great Shine Window Cleaning  43.783145 -79.157431   
2 -79.160497         Royal Canadian Legion  43.782533 -79.163085   
3 -79.188711                RBC Royal Bank  43.766790 -79.191151   
4 -79.188711             G & G Electronics  43.765309 -79.191537   
5 -79.188711              Big Bite Burrito  43.766299 -79.190720   
6 -79.188711         Enterprise Rent-A-Car  43.764076 -79.193406   
7 -79.188711      Wood Floor Polishing Inc  43.766500 -79.185207   
8 -79.188711         Woburn Medical Centre  43.766631 -79.192286   
9 -79.188711  Lawrence Ave E & Kingston Rd  43.767704 -79.189490   

                      8  
0  Fast Food Restaurant  
1          Home Service  
2                   Bar  
3                  Bank  
4     Electronics Store  
5    Mexican Restaurant  
6   Rental Car Location  
7         Moving Target  
8        Medical Center  
9          Intersection

In [31]:
venues

[('M1B',
  'Scarborough',
  'Malvern, Rouge',
  43.806686299999996,
  -79.19435340000001,
  'Wendy’s',
  43.80744841934756,
  -79.19905558052072,
  'Fast Food Restaurant'),
 ('M1C',
  'Scarborough',
  'Rouge Hill, Port Union, Highland Creek',
  43.7845351,
  -79.16049709999999,
  'Great Shine Window Cleaning',
  43.7831452,
  -79.1574307,
  'Home Service'),
 ('M1C',
  'Scarborough',
  'Rouge Hill, Port Union, Highland Creek',
  43.7845351,
  -79.16049709999999,
  'Royal Canadian Legion',
  43.78253332838298,
  -79.16308473261682,
  'Bar'),
 ('M1E',
  'Scarborough',
  'Guildwood, Morningside, West Hill',
  43.7635726,
  -79.1887115,
  'RBC Royal Bank',
  43.76678992471017,
  -79.19115118872593,
  'Bank'),
 ('M1E',
  'Scarborough',
  'Guildwood, Morningside, West Hill',
  43.7635726,
  -79.1887115,
  'G & G Electronics',
  43.765309,
  -79.191537,
  'Electronics Store'),
 ('M1E',
  'Scarborough',
  'Guildwood, Morningside, West Hill',
  43.7635726,
  -79.1887115,
  'Big Bite Burrito',
  

In [32]:
df_venues.columns = ['PostalCode', 'Borough', 'Neighborhood', 'BoroughLatitude',' BoroughLongitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']
print(df_venues.shape)
df_venues.head()

(2132, 9)


PostalCode      Borough                            Neighborhood  \
0        M1B  Scarborough                          Malvern, Rouge   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek   
2        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek   
3        M1E  Scarborough       Guildwood, Morningside, West Hill   
4        M1E  Scarborough       Guildwood, Morningside, West Hill   

   BoroughLatitude   BoroughLongitude                    VenueName  \
0        43.806686         -79.194353                      Wendy’s   
1        43.784535         -79.160497  Great Shine Window Cleaning   
2        43.784535         -79.160497        Royal Canadian Legion   
3        43.763573         -79.188711               RBC Royal Bank   
4        43.763573         -79.188711            G & G Electronics   

   VenueLatitude  VenueLongitude         VenueCategory  
0      43.807448      -79.199056  Fast Food Restaurant  
1      43.783145      -79.157431          Home Service  
2      43.782533      -79.163085                   Bar  
3      43.766790      -79.191151                  Bank  
4      43.765309      -79.191537     Electronics Store

In [33]:
df_venues.groupby(['PostalCode', 'Borough', 'Neighborhood'])['VenueName'].count()

PostalCode  Borough           Neighborhood                                                                                                                          
M1B         Scarborough       Malvern, Rouge                                                                                                                              1
M1C         Scarborough       Rouge Hill, Port Union, Highland Creek                                                                                                      2
M1E         Scarborough       Guildwood, Morningside, West Hill                                                                                                           8
M1G         Scarborough       Woburn                                                                                                                                      3
M1H         Scarborough       Cedarbrae                                                                                                            

Analyzing each area

In [34]:
toronto = pd.get_dummies(df_venues[['VenueCategory']], prefix="", prefix_sep="")

toronto['PostalCode'] = df_venues['PostalCode']
toronto['Borough'] = df_venues['Borough']
toronto['Neighborhoods'] = df_venues['Neighborhood']

fixCol = list(toronto.columns[-3:]) + list(toronto.columns[:-3])
toronto = toronto[fixCol]

toronto.head(10)


PostalCode      Borough                           Neighborhoods  \
0        M1B  Scarborough                          Malvern, Rouge   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek   
2        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek   
3        M1E  Scarborough       Guildwood, Morningside, West Hill   
4        M1E  Scarborough       Guildwood, Morningside, West Hill   
5        M1E  Scarborough       Guildwood, Morningside, West Hill   
6        M1E  Scarborough       Guildwood, Morningside, West Hill   
7        M1E  Scarborough       Guildwood, Morningside, West Hill   
8        M1E  Scarborough       Guildwood, Morningside, West Hill   
9        M1E  Scarborough       Guildwood, Morningside, West Hill   

   Accessories Store  Afghan Restaurant  Airport  Airport Food Court  \
0                  0                  0        0                   0   
1                  0                  0        0                   0   
2                  0                  0        0                   0   
3                  0                  0        0                   0   
4                  0                  0        0                   0   
5                  0                  0        0                   0   
6                  0                  0        0                   0   
7                  0                  0        0                   0   
8                  0                  0        0                   0   
9                  0                  0        0                   0   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0             0               0                0                 0   
1             0               0                0                 0   
2             0               0                0                 0   
3             0               0                0                 0   
4             0               0                0                 0   
5             0               0                0                 0   
6             0               0                0                 0   
7             0               0                0                 0   
8             0               0                0                 0   
9             0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                    0             0         0            0           0   
1                    0             0         0            0           0   
2                    0             0         0            0           0   
3                    0             0         0            0           0   
4                    0             0         0            0           0   
5                    0             0         0            0           0   
6                    0             0         0            0           0   
7                    0             0         0            0           0   
8                    0             0         0            0           0   
9                    0             0         0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   
5                    0                 0                   0            0   
6                    0                 0                   0            0   
7                    0                 0                   0            0   
8                    0                 0                   0            0   
9                    0                 0                   0            0   

   A

In [35]:
toronto_grouped = toronto.groupby('Borough').mean().reset_index()

toronto_grouped

Borough  Accessories Store  Afghan Restaurant   Airport  \
0   Central Toronto           0.000000           0.000000  0.000000   
1  Downtown Toronto           0.000000           0.000816  0.000816   
2      East Toronto           0.000000           0.000000  0.000000   
3         East York           0.000000           0.000000  0.000000   
4         Etobicoke           0.000000           0.000000  0.000000   
5       Mississauga           0.000000           0.000000  0.000000   
6        North York           0.004082           0.000000  0.004082   
7       Scarborough           0.000000           0.000000  0.000000   
8      West Toronto           0.000000           0.000000  0.000000   
9              York           0.000000           0.000000  0.000000   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0            0.000000      0.000000        0.000000         0.000000   
1            0.000816      0.000816        0.001631         0.001631   
2            0.000000      0.000000        0.000000         0.000000   
3            0.000000      0.000000        0.000000         0.000000   
4            0.000000      0.000000        0.000000         0.000000   
5            0.000000      0.000000        0.000000         0.000000   
6            0.000000      0.000000        0.000000         0.000000   
7            0.000000      0.000000        0.000000         0.000000   
8            0.000000      0.000000        0.000000         0.000000   
9            0.000000      0.000000        0.000000         0.000000   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0          0.000000             0.017391      0.000000  0.000000     0.000000   
1          0.000816             0.013866      0.001631  0.004078     0.008972   
2          0.000000             0.024000      0.000000  0.000000     0.000000   
3          0.000000             0.000000      0.000000  0.000000     0.000000   
4          0.000000             0.014286      0.000000  0.000000     0.000000   
5          0.000000             0.076923      0.000000  0.000000     0.000000   
6          0.000000             0.008163      0.000000  0.000000     0.004082   
7          0.000000             0.011236      0.000000  0.000000     0.000000   
8          0.000000             0.000000      0.006369  0.000000     0.006369   
9          0.000000             0.000000      0.000000  0.000000     0.000000   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0    0.000000             0.000000          0.000000            0.008696   
1    0.001631             0.003263          0.006525            0.000816   
2    0.000000             0.000000          0.000000            0.000000   
3    0.000000             0.000000          0.000000            0.026667   
4    0.000000             0.000000          0.000000            0.000000   
5    0.000000             0.000000          0.000000            0.000000   
6    0.000000             0.004082          0.016327            0.008163   
7    0.000000             0.000000          0.000000            0.011236   
8    0.000000             0.012739          0.012739            0.000000   
9    0.000000             0.000000          0.000000            0.000000   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop    Bakery  \
0     0.000000          0.000   0.008696    0.000000    0.008696  0.000000   
1     0.000000          0.000   0.002447    0.000816    0.001631  0.021207   
2     0.000000          0.008   0.000000    0.000000    0.000000  0.024000   
3     0.000000          0.000   0.000000    0.000000    0.013333  0.000000   
4     0.000000          0.000   0.000000    0.000000    0.000000  0.028571   
5     0.000000          0.000   0.000000    0.000000    0.000000  0.000000   
6     0.000000          0.000   0.000000    0.000000    0.000000  0.012245   
7     0.011236          0.000   0.000000    0.000000    0.000000  0.044944   
8     

In [36]:
toronto_grouped.shape

(10, 271)

## Getting most occurence venues
Now we want to get 10 most occurence venues in each area

In [37]:
def return_most_common_venues(row, top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:top_venues]

In [38]:

top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Borough']
for ind in np.arange(top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
torontoVenuesSorted = pd.DataFrame(columns=columns)
torontoVenuesSorted['Borough'] = toronto_grouped['Borough']

for ind in np.arange(toronto_grouped.shape[0]):
    torontoVenuesSorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], top_venues)

torontoVenuesSorted.head()

Borough 1st Most Common Venue 2nd Most Common Venue  \
0   Central Toronto           Coffee Shop           Pizza Place   
1  Downtown Toronto           Coffee Shop                  Café   
2      East Toronto      Greek Restaurant           Coffee Shop   
3         East York           Coffee Shop                  Bank   
4         Etobicoke           Pizza Place        Sandwich Place   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Sandwich Place                  Park                  Café   
1            Restaurant                 Hotel   Japanese Restaurant   
2    Italian Restaurant               Brewery                  Café   
3           Pizza Place              Pharmacy                  Park   
4           Coffee Shop              Pharmacy        Discount Store   

  6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
0      Sushi Restaurant                     Pub          Dessert Shop   
1    Italian Restaurant                  Bakery                  Park   
2        Ice Cream Shop    Fast Food Restaurant        Sandwich Place   
3          Burger Joint  Furniture / Home Store  Fast Food Restaurant   
4  Fast Food Restaurant           Grocery Store                   Gym   

  9th Most Common Venue 10th Most Common Venue  
0            Restaurant                    Gym  
1                   Gym       Sushi Restaurant  
2           Pizza Place             Restaurant  
3          Skating Rink             Restaurant  
4                Bakery    Fried Chicken Joint

## K-mean algorithm usage
Using the K-mean algorithm to to cluster the boroughs

In [39]:
clusters = 2

torontoClustering = toronto_grouped.drop('Borough',1)

kmeans = KMeans(n_clusters = clusters, random_state = 0).fit(torontoClustering)
kmeans.labels_[0:10]

array([1, 1, 1, 1, 1, 0, 1, 1, 1, 1], dtype=int32)

In [40]:
torontoVenuesSorted.insert(0, 'Cluster Lables', kmeans.labels_)

torontoMerged = df_venues

torontoMerged = torontoMerged.join(torontoVenuesSorted.set_index('Borough'), on='Borough')

torontoMerged.head(10)

PostalCode      Borough                            Neighborhood  \
0        M1B  Scarborough                          Malvern, Rouge   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek   
2        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek   
3        M1E  Scarborough       Guildwood, Morningside, West Hill   
4        M1E  Scarborough       Guildwood, Morningside, West Hill   
5        M1E  Scarborough       Guildwood, Morningside, West Hill   
6        M1E  Scarborough       Guildwood, Morningside, West Hill   
7        M1E  Scarborough       Guildwood, Morningside, West Hill   
8        M1E  Scarborough       Guildwood, Morningside, West Hill   
9        M1E  Scarborough       Guildwood, Morningside, West Hill   

   BoroughLatitude   BoroughLongitude                     VenueName  \
0        43.806686         -79.194353                       Wendy’s   
1        43.784535         -79.160497   Great Shine Window Cleaning   
2        43.784535         -79.160497         Royal Canadian Legion   
3        43.763573         -79.188711                RBC Royal Bank   
4        43.763573         -79.188711             G & G Electronics   
5        43.763573         -79.188711              Big Bite Burrito   
6        43.763573         -79.188711         Enterprise Rent-A-Car   
7        43.763573         -79.188711      Wood Floor Polishing Inc   
8        43.763573         -79.188711         Woburn Medical Centre   
9        43.763573         -79.188711  Lawrence Ave E & Kingston Rd   

   VenueLatitude  VenueLongitude         VenueCategory  Cluster Lables  \
0      43.807448      -79.199056  Fast Food Restaurant               1   
1      43.783145      -79.157431          Home Service               1   
2      43.782533      -79.163085                   Bar               1   
3      43.766790      -79.191151                  Bank               1   
4      43.765309      -79.191537     Electronics Store               1   
5      43.766299      -79.190720    Mexican Restaurant               1   
6      43.764076      -79.193406   Rental Car Location               1   
7      43.766500      -79.185207         Moving Target               1   
8      43.766631      -79.192286        Medical Center               1   
9      43.767704      -79.189490          Intersection               1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                  Bank           Coffee Shop                Bakery   
1                  Bank           Coffee Shop                Bakery   
2                  Bank           Coffee Shop                Bakery   
3                  Bank           Coffee Shop                Bakery   
4                  Bank           Coffee Shop                Bakery   
5                  Bank           Coffee Shop                Bakery   
6                  Bank           Coffee Shop                Bakery   
7                  Bank           Coffee Shop                Bakery   
8                  Bank           Coffee Shop                Bakery   
9                  Bank           Coffee Shop                Bakery   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Breakfast Spot    Chinese Restaurant              Pharmacy   
1        Breakfast Spot    Chinese Restaurant              Pharmacy   
2        Breakfast Spot    Chinese Restaurant              Pharmacy   
3        Breakfast Spot    Chinese Restaurant              Pharmacy   
4        Breakfast Spot    Chinese Restaurant              Pharmacy   
5        Breakfast Spot    Chinese Restaurant              Pharmacy   
6        Breakfast Spot    Chinese Restaurant              Pharmacy   
7        Breakfast Spot    Chinese Restaurant              Pharmacy   
8        Breakfast Spot    Chinese Restaurant              Pharmacy   
9        Breakfast Spot    Chinese Restaurant              Pharmacy   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0  Fast Fo

In [42]:
torontoMerged

PostalCode           Borough  \
0           M1B       Scarborough   
1           M1C       Scarborough   
2           M1C       Scarborough   
3           M1E       Scarborough   
4           M1E       Scarborough   
5           M1E       Scarborough   
6           M1E       Scarborough   
7           M1E       Scarborough   
8           M1E       Scarborough   
9           M1E       Scarborough   
10          M1E       Scarborough   
11          M1G       Scarborough   
12          M1G       Scarborough   
13          M1G       Scarborough   
14          M1H       Scarborough   
15          M1H       Scarborough   
16          M1H       Scarborough   
17          M1H       Scarborough   
18          M1H       Scarborough   
19          M1H       Scarborough   
20          M1H       Scarborough   
21          M1H       Scarborough   
22          M1J       Scarborough   
23          M1J       Scarborough   
24          M1K       Scarborough   
25          M1K       Scarborough   
26          M1K       Scarborough   
27          M1K       Scarborough   
28          M1K       Scarborough   
29          M1L       Scarborough   
30          M1L       Scarborough   
31          M1L       Scarborough   
32          M1L       Scarborough   
33          M1L       Scarborough   
34          M1L       Scarborough   
35          M1L       Scarborough   
36          M1L       Scarborough   
37          M1M       Scarborough   
38          M1M       Scarborough   
39          M1N       Scarborough   
40          M1N       Scarborough   
41          M1N       Scarborough   
42          M1N       Scarborough   
43          M1P       Scarborough   
44          M1P       Scarborough   
45          M1P       Scarborough   
46          M1P       Scarborough   
47          M1P       Scarborough   
48          M1P       Scarborough   
49          M1R       Scarborough   
50          M1R       Scarborough   
51          M1R       Scarborough   
52          M1R       Scarborough   
53          M1R       Scarborough   
54          M1R       Scarborough   
55          M1R       Scarborough   
56          M1S       Scarborough   
57          M1S       Scarborough   
58          M1S       Scarborough   
59          M1S       Scarborough   
60          M1T       Scarborough   
61          M1T       Scarborough   
62          M1T       Scarborough   
63          M1T       Scarborough   
64          M1T       Scarborough   
65          M1T       Scarborough   
66          M1T       Scarborough   
67          M1T       Scarborough   
68          M1T       Scarborough   
69          M1T       Scarborough   
70          M1T       Scarborough   
71          M1T       Scarborough   
72          M1T       Scarborough   
73          M1T       Scarborough   
74          M1V       Scarborough   
75          M1V       Scarborough   
76          M1W       Scarborough   
77          M1W       Scarborough   
78          M1W       Scarborough   
79          M1W       Scarborough   
80          M1W       Scarborough   
81          M1W       Scarborough   
82          M1W       Scarborough   
83          M1W       Scarborough   
84          M1W       Scarborough   
85          M1W       Scarborough   
86          M1W       Scarborough   
87          M1W       Scarborough   
88          M1W       Scarborough   
89          M2H        North York   
90          M2H        North York   
91          M2H        North York   
92          M2H        North York   
93          M2H        North York   
94          M2J        North York   
95          M2J        North York   
96          M2J        North York   
97          M2J        North York   
98          M2J        North York   
99          M2J        North York   
100         M2J        North York   
101         M2J        North York   
102         M2J        North York   
103         M2J        North York   
104         M2J        North York   
105         M2J        North York   
106         M2J        North York   
107      

## Creating second map with folium
Creating map to see clusters visualized

In [41]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(clusters)
ys = [i+x+(i*x)**2 for i in range(clusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, post, bor, poi, cluster in zip(torontoMerged['VenueLatitude'], torontoMerged['VenueLongitude'], torontoMerged['PostalCode'], torontoMerged['Borough'], torontoMerged['Neighborhood'], torontoMerged['Cluster Lables']):
    label = folium.Popup('{} ({}): {} - Cluster {}'.format(bor, post, poi, cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters


# Conclusion about boroughs in Toronto
Cluster 1: Mostly Greek or coffee shops which are seen in east downtown west Toronto 
Cluster 0: Mostly hotels.